# Kaggle survey

Info about the competition: https://www.kaggle.com/competitions/kaggle-survey-2022/overview


In [1]:
#!pip install ipyvizzu
#!pip install ipyvizzu-story

In [2]:
import pandas as pd
import numpy as np

from ipyvizzu import Chart, Data, Config, Style
from ipyvizzustory import Story, Slide, Step

#Create data object, read csv to data frame and add data frame to data object.
data = Data()

#Only use columns you'll need for your story - should be updated to match the story content
col_list = ['Q2','Q3','Q5','Q25','Q29','Q23']

df = pd.read_csv("../data/Kaggle/kaggle_survey_2022_responses.csv", usecols=col_list)
pd.set_option('display.max_columns', None)



#Add count column
df['Count'] = 1
df['Q25'] = df['Q25'].str.replace('employees','')
df.head()

Q2                                      Q3  \
0  What is your age (# years)?  What is your gender? - Selected Choice   
1                        30-34                                     Man   
2                        30-34                                     Man   
3                        18-21                                     Man   
4                        55-59                                     Man   

                                                  Q5  \
0  Are you currently a student? (high school, uni...   
1                                                 No   
2                                                 No   
3                                                Yes   
4                                                 No   

                                                 Q23  \
0  Select the title most similar to your current ...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                     Data Scientist   

                                                 Q25  \
0  What is the size of the company where you are ...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                              0-49    

                                                 Q29  Count  
0  What is your current yearly compensation (appr...      1  
1                                                NaN      1  
2                                                NaN      1  
3                                                NaN      1  
4                                      25,000-29,999      1

In [3]:
#Remove row with question texts
df = df.drop(0)

#List unique answers for Q2
df.Q25.unique()

array([nan, '0-49 ', '250-999 ', '1000-9,999 ', '10,000 or more ',
       '50-249 '], dtype=object)

In [4]:
#Add new column categorizing respondents with ages above and below 30
df.insert(2,'below_30',np.where((df.Q2 == '18-21') | (df.Q2 == '22-24') | (df.Q2 == '25-29'), "below 30", "above 30"))
df['below_30'] = df['below_30'].astype(str)

In [5]:
#prepare to sort the dataframe by salary list
salarysorter = ['$0-999', '1,000-1,999', '2,000-2,999', '3,000-3,999', '4,000-4,999', '5,000-7,499', '7,500-9,999', '10,000-14,999', '15,000-19,999', '20,000-24,999', '25,000-29,999', '30,000-39,999', '40,000-49,999', '50,000-59,999', '60,000-69,999', '70,000-79,999', '80,000-89,999', '90,000-99,999', '100,000-124,999', '125,000-149,999', '150,000-199,999', '200,000-249,999', '250,000-299,999', '300,000-499,999', '$500,000-999,999', '>$1,000,000', 'NaN']

# Create the dictionary that defines the order for sorting
sorterIndex = dict(zip(salarysorter, range(len(salarysorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Salary_Rank'] = df['Q29'].map(sorterIndex)

#sorting is done together with the titles (Q23)

In [6]:
#sort the dataframe by company size
sizesorter = ['0-49', '50-249', '250-999', '1000-9,999', '10,000 or more', 'NaN']

# Create the dictionary that defines the order for sorting
sorterIndex3 = dict(zip(sizesorter, range(len(sizesorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Size_Rank'] = df['Q25'].map(sorterIndex)

In [7]:
df.Q23.unique()

array([nan, 'Data Scientist', 'Software Engineer', 'Research Scientist',
       'Other', 'Developer Advocate',
       'Data Analyst (Business, Marketing, Financial, Quantitative, etc)',
       'Data Engineer', 'Currently not employed',
       'Machine Learning/ MLops Engineer', 'Engineer (non-software)',
       'Teacher / professor', 'Statistician',
       'Manager (Program, Project, Operations, Executive-level, etc)',
       'Data Administrator', 'Data Architect'], dtype=object)

In [8]:
#sort the dataframe by title
titlesorter = ['Data Scientist', 'Data Analyst', 'Software Engineer', 'Teacher / professor', 'Manager', 'Other', 'Research Scientist', 'ML / MLops Engineer', 'Engineer (non-software)', 'Data Engineer', 'Statistician', 'Data Architect', 'Data Administrator', 'Developer Advocate', 'Currently not employed',]

#replace long titles with shorter versions
df = df.replace("Data Analyst (Business, Marketing, Financial, Quantitative, etc)", "Data Analyst")
df = df.replace("Manager (Program, Project, Operations, Executive-level, etc)", "Manager")
df = df.replace("Machine Learning/ MLops Engineer", "ML / MLops Engineer")

# Create the dictionary that defines the order for sorting
sorterIndex2 = dict(zip(titlesorter, range(len(titlesorter))))

# Generate a rank column that will be used to sort
# the dataframe numerically
df['Title_Rank'] = df['Q23'].map(sorterIndex2)

df.sort_values(['Salary_Rank','Title_Rank','Size_Rank'], inplace = True)


In [9]:
#Add percentage value for gender categories for each age group
df['Gender_added'] = df['Q3'].notna()
df['Gender_added'] = df['Gender_added'].astype(str)
df['Gender_Pct[%]'] = 100 / df.groupby(['below_30','Gender_added'])['Count'].transform('sum') 

In [10]:
#Add percentage value for salary categories for each age group
df['Employee_w_salary'] = df['Q29'].notna()
df['Employee_w_salary'] = df['Employee_w_salary'].astype(str)
df['Salary_Pct[%]'] = 100 / df.groupby(['below_30','Employee_w_salary'])['Count'].transform('sum')


In [11]:
#Add percentage share value between age groups for each title
df['Employee_w_title'] = df['Q23'].notna()
df['Employee_w_title'] = df['Employee_w_title'].astype(str)
df['Title_Pct[%]'] = 100 / df.groupby(['Q23','Employee_w_title'])['Count'].transform('sum')


In [12]:
#Add column to seperate those that did not add company size
df['Employee_c_size'] = df['Q23'].notna()
df['Employee_c_size'] = df['Employee_c_size'].astype(str)

display(df)

Q2     Q3  below_30   Q5             Q23       Q25     Q29  Count  \
115    30-34    Man  above 30   No  Data Scientist     0-49   $0-999      1   
255    30-34  Woman  above 30   No  Data Scientist   50-249   $0-999      1   
329    22-24  Woman  below 30   No  Data Scientist  250-999   $0-999      1   
839    30-34    Man  above 30   No  Data Scientist     0-49   $0-999      1   
1168   25-29    Man  below 30   No  Data Scientist     0-49   $0-999      1   
...      ...    ...       ...  ...             ...       ...     ...    ...   
23989  55-59    Man  above 30  Yes             NaN       NaN     NaN      1   
23992  22-24    Man  below 30  Yes             NaN       NaN     NaN      1   
23993  22-24    Man  below 30  Yes             NaN       NaN     NaN      1   
23994  60-69    Man  above 30  Yes             NaN       NaN     NaN      1   
23997  18-21    Man  below 30  Yes             NaN       NaN     NaN      1   

       Salary_Rank  Size_Rank  Title_Rank Gender_added  Gender_Pct[%]  \
115            0.0        NaN         0.0         True       0.009361   
255            0.0        NaN         0.0         True       0.009361   
329            0.0        NaN         0.0         True       0.007511   
839            0.0        NaN         0.0         True       0.009361   
1168           0.0        NaN         0.0         True       0.007511   
...            ...        ...         ...          ...            ...   
23989          NaN        NaN         NaN         True       0.009361   
23992          NaN        NaN         NaN         True       0.007511   
23993          NaN        NaN         NaN         True       0.007511   
23994          NaN        NaN         NaN         True       0.009361   
23997          NaN        NaN         NaN         True       0.007511   

      Employee_w_salary  Salary_Pct[%] Employee_w_title  Title_Pct[%]  \
115                True       0.017525             True       0.05184   
255                True       0.017525             True       0.05184   
329                True       0.041152             True       0.05184   
839                True       0.017525             True       0.05184   
1168               True       0.041152             True       0.05184   
...                 ...            ...              ...           ...   
23989             False       0.020092            False           NaN   
23992             False       0.009188            False           NaN   
23993             False       0.009188            False           NaN   
23994             False       0.020092            False           NaN   
23997             False       0.009188            False           NaN   

      Employee_c_size  
115              True  
255              True  
329              True  
839              True  
1168             True  
...               ...  
23989           False  
23992           False  
23993           False  
23994           False  
23997           False  

[23997 rows x 18 columns]

In [13]:
style = Style(
    {
        "legend": {"width":"14em" },
        'fontSize' : '140%',
        'plot' : {'marker' :{ 'label' :{ 'fontSize' : '100%'},
                            'maxLightness' : 0},
                            }},
)

In [14]:
data.add_data_frame(df)
story = Story(data=data, style=style)
story.set_size("100%", "400px")
story.set_feature("tooltip", True)

#Add event to avoid small values written on the label scale as they overlap
label_handler_method = "if(event.data.text < 120) event.preventDefault()"
#story.add_event("plot-marker-label-draw", label_handler_method)

slide0 = Slide(
#Show number of respondents
    Step(
        Config.bar({
            "x": "Count",
          #  "reverse": True,
            "title": "No. of respondents",

        })
    )
)
story.add_slide(slide0)

slide1 = Slide()
#Show number of respondents below and above 30
slide1.add_step(
    Step(
        Config.bar({
            "x": ["Count","below_30"]
        })
))

slide1.add_step(
    Step(
        Config.bar({
            "x": "Count",
            "y": "below_30",
            "title": "No. of respondents below and above 30 years"
        })
    )
)
story.add_slide(slide1)

#Add gender
slide2 = Slide()

slide2.add_step(
    Step(
        Config({
            "x": ["Count","Q3"],
            "y": "below_30",
        })
    )
)

slide2.add_step(
    Step(
        Config({
            "color":"Q3",
        }),
    )
)

story.add_slide(slide2)
    

#Show ratio of genders
slide3 = Slide(
    Step(
        Config({
            'align':'stretch',
            'label':'Gender_Pct[%]',
            "title": "Share of respondents below and above 30 years"
        })
    )
)
story.add_slide(slide3)

In [15]:
#Remove gender
slide4 = Slide()

slide4.add_step(
    Step(
        Config({
            "align": "none",
            "label": "Count"
        })
    )
)

slide4.add_step(
    Step(
        Config({
            "x":"Count",
            "color":None
        }),
    )
)

story.add_slide(slide4)

#Add student status
slide5 = Slide()

slide5.add_step(
    Step(
        Config.stackedBar({
            "x": "Count",
            "y": "below_30",
            "stackedBy":"Q5",
            "title": "Are you currently a student?"
        })
    )
)

story.add_slide(slide5)

#Zoom to those who are not students anymore
slide6 = Slide()

slide6.add_step(
    Step(
        Data.filter("record.Q5 == 'No'"),
        Config({
            "title": "Zoom to employees"
        })
    )
)

slide6.add_step(
    Step(
        Config({
            "color": "below_30",
            "legend":"color"
        }),
        Style({
            "plot": {
                "marker": {
                    "colorPalette": "#26EC87FF #29B9BFFF",
                }}
        })
    )
)

story.add_slide(slide6)
# Play the created story - should be at the end of the cell
#story.play()

In [16]:
slide6_1 = Slide()
slide6_1.add_step(
    Step(
        Config({
            "x": ["Count","Employee_c_size"],
            "lightness": "Employee_c_size",
            "legend":"color",
            "title": "Remove those who did not add company size",
        })
    )
)

slide6_1.add_step(
    Step(
        Data.filter("record.Q5 === 'No' && record.Q25 !== ''" ),
        Config({
            "lightness":None
        })
    )
)

story.add_slide(slide6_1)

slide6_2 = Slide()
slide6_2.add_step(
    Step(
        Config({
            "x": ["Count","Q25"],
        })
    )
)

slide6_2.add_step(
    Step(
        Config.stackedBubble(({
            "size": "Count",
            "color": "below_30",
            "stackedBy": "Q25",
        })
    )
))

slide6_2.add_step(
    Step(
        Config(({
            "label": ["Q25","Count"],
            "title": "",
        })
    )
))

story.add_slide(slide6_2)


slide6_4 = Slide()
slide6_4.add_step(
    Step(
        Config(({
            "size":None,
            "noop":None,
            "x":["Count","Q25"],
            "y":"below_30",
            "label":"Count",
            "title": "",
            "geometry":"rectangle"
        })
    )
))

slide6_4.add_step(
    Step(
        Config(({
            "x": ["Count","Employee_c_size"],
            "lightness": "Employee_c_size",
            "y":"below_30",
            "title": "Show respondents with no employer size",
        })
    )
))

slide6_4.add_step(
    Step(
        Data.filter("record.Q5 === 'No'" ),
        Config(({
            "x": ["Count","Employee_c_size"],
            "lightness": "Employee_c_size",
            "title": "Show respondents with no employer size",
        })
    )
))

slide6_4.add_step(
    Step(
        Config(({
            "x": "Count",
            "lightness": None,
        })
    )
))

story.add_slide(slide6_4)

In [17]:
slide7 = Slide()

slide7.add_step(
    Step(
        Config({
            "x": ["Count","Employee_w_salary"],
            "title": "Remove those who did not provide salary info",
            "lightness": "Employee_w_salary"
        })
    )
)

slide7.add_step(
    Step(
        Data.filter("record.Q5 === 'No' && record.Q29 !== ''" ),
        Config({
            "lightness":None
        })
    )
)


story.add_slide(slide7)

slide8 = Slide()
slide8.add_step(
    Step(
        Config({
            "x": ["Count","Q29"],
            "legend": "color",
            "label":None,
        }),
        Style({
            "plot": {
                "marker": {
                    'label' :{ 'fontSize' : '0.7em'},
                    },
                'xAxis' :{ 'label' :{ 'angle' : '-3.5', 'fontSize' : '0.7em'}
                    }
            }
        })
    )
)

slide8.add_step(
    Step(
        Config.splittedColumn({
            "y":"Salary_Pct[%]",
            "x":"Q29",
            "splittedBy":"below_30",
            "title":"Salary Distribution",
        })
    )
)
slide8.add_step(
    Step(
        Config({
            "label":"Salary_Pct[%]"
        })
    )
)


story.add_slide(slide8)
# Play the created story - should be at the end of the cell
#story.play()

In [19]:
slide11 = Slide()

slide11.add_step(
    Step(
        Config({
            "x": ["Count","Q29"],
            "y": "below_30",
            "title": "Let's put back those who didn't provide a salary",
            "split": False
        }),
        Style({"plot": {"marker": {'label' :{ 'fontSize' : '100%'}}}})
))

slide11.add_step(
    Step(
        Config({
            "label": "Count",
            "x": ["Count","Employee_w_salary"],
            "lightness": "Employee_w_salary",
        })
    )
)


slide11.add_step(
    Step(
        Data.filter("record.Q5 === 'No'"),
        Config({
            "x":"Count",
            "lightness":None,
            "title": "And filter the ones that did not add a title"
        })
    )
)

slide11.add_step(
    Step(
        Config({
            "x": ["Count","Employee_w_title"],
            "lightness": "Employee_w_title",
        })
    )
)

slide11.add_step(
    Step(
    Data.filter("record.Q5 === 'No' && record.Q23 !== ''" ),
))

story.add_slide(slide11)

slide12 = Slide()

slide12.add_step(
    Step(
        Config({
            "x": ["Count","Q23"],
            "label": None
        })
    )
)

slide12.add_step(
    Step(
        Config({
            "x": "Q23",
            "y": ["below_30","Count"],
            "label":"Count",
            "title":"Job titles"
        }),
        Style({"plot": {"marker": {'label' :{ 'fontSize' : '0.7em'}}}})
    )
)

story.add_slide(slide12)


slide13 = Slide()
slide13.add_step(
    Step(
        Config({
            "y": ["below_30","Title_Pct[%]"],
            "label":"Title_Pct[%]",
            "title":"Job titles (%)"
        })
    )
)
story.add_slide(slide13)

# Play the created story - should be at the end of the cell
story.play()

In [ ]:
# If you want to save the story as an interactive HTML
# (containing only the output of the previous cell),
# use the following command:
story.export_to_html(filename="kaggle.html")

### Learn more about [ipyvizzu-story](https://github.com/vizzuhq/ipyvizzu-story/)